In [25]:
#!pip install pytesseract
from PIL import Image
import pandas as pd
import pytesseract
from pytesseract import Output
import pandas as pd

In [26]:
#!pip install pyarrow

In [27]:
df = pd.read_parquet('./testing.parquet')

In [28]:
df.head()

image  \
0  b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\...   
1  b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\...   
2  b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\...   
3  b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\...   
4  b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\...   

                                ocr_annotation_texts  image_height  \
0  71 2 84 11 \n43 7 57 9 PROJECT BRIEF\n14 11 19...          1000   
1  3 3 11 10 B&W\n77 3 87 10 QUALITY\n15 4 74 9 Q...          1000   
2  12 11 15 13 TO:\n24 11 34 13 R. B. SPELL\n64 1...          1000   
3  28 6 73 9 SPORTS MARKETING ENTERPRISES DOCUMEN...          1000   
4  18 8 25 9 S.P. Zolot\n2 8 5 9 TO:\n60 8 73 10 ...          1000   

   image_width  
0          762  
1          762  
2          754  
3          795  
4          754

In [29]:
import numpy as np
import io
import cv2

In [30]:
pytesseract.pytesseract.tesseract_cmd = r'/opt/homebrew/bin/tesseract'



class ocr:
    def __init__(self, df):
        self.df = df
    def get_data(self, n):
        image = Image.open(io.BytesIO(self.df.iloc(0)[n]['image']))
        image_height = self.df.iloc(0)[n]['image_height']
        image_width = self.df.iloc(0)[n]['image_width']
        image_data = pytesseract.image_to_data(image, output_type=Output.DICT)
        txt = ''
        
        for i in range(len(image_data['level'])):
            if image_data['text'][i] == '':
                continue
            txt += image_data['text'][i]
            txt += ' ' + str(image_data['left'][i]) + ' ' + str(image_data['top'][i]) + ' ' + str(image_data['width'][i]) + ' ' + str(image_data['height'][i]) + ' '
        return image, image_height, image_width, image_data, txt
    def sort_bounding_boxes(self, img_data, img_height, img_width):
        n_boxes = len(img_data['text'])
        if n_boxes == 0:
            return []
        #print(n_boxes)
        boxes = []
        for i in range(n_boxes):
            box = {
                'index': i,
                'text': img_data['text'][i],
                'left': img_data['left'][i],
                'top': img_data['top'][i],
                'width': img_data['width'][i],
                'height': img_data['height'][i]
            }
            boxes.append(box)
    
        
        sorted_boxes = sorted(boxes, key=lambda x: (x['top'], x['left']))
       
        final_boxes = []
        for i in range(len(sorted_boxes)):
            if (
                sorted_boxes[i]['left'] >= img_width * 0.9
                or sorted_boxes[i]['top'] >= img_height * 0.9
            ):
                continue
            else:
                final_boxes.append(sorted_boxes[i])
        return final_boxes
    def ocr_parse(self, img_data, img_height, img_width, width_threshold_percent=2, height_threshold_percent=1):
        parsed_boxes = []

        if not img_data:
            return parsed_boxes

        current_box = img_data[0]
        img_width = max(current_box['left'] + current_box['width'], 1)
        img_height = max(current_box['top'] + current_box['height'], 1)
        current_text = current_box['text']

        for i in range(1, len(img_data)):
            width_threshold = img_width * width_threshold_percent / 100
            height_threshold = img_height * height_threshold_percent / 100

            if (
                img_data[i]['left'] - (current_box['left'] + current_box['width']) <= width_threshold
                and abs(img_data[i]['top'] - current_box['top']) <= height_threshold
            ):
                current_box['width'] = img_data[i]['left'] + img_data[i]['width'] - current_box['left']
                current_box['height'] = max(current_box['height'], img_data[i]['top'] + img_data[i]['height'] - current_box['top'])
                current_text += ' ' + img_data[i]['text']
            else:
                current_box['text'] = current_text
                parsed_boxes.append(current_box)
                current_box = img_data[i]
                current_text = current_box['text']

        current_box['text'] = current_text
        parsed_boxes.append(current_box)

        return parsed_boxes
    def view(self, n):
        image, img_height, img_width, img_data, text = self.get_data(n)
        img_str = self.df.iloc(0)[n]['image']
        nparr = np.fromstring(img_str, np.uint8)
        img_np = cv2.imdecode(nparr, flags=1)
    
        n_boxes = len(img_data['level'])
        for i in range(n_boxes):
            (x, y, w, h) = (img_data['left'][i], img_data['top'][i], img_data['width'][i], img_data['height'][i])
    
        sorted_boxes = self.sort_bounding_boxes(img_data, img_height, img_width)
        parsed_boxes = self.ocr_parse(sorted_boxes, img_width, img_height)
        
        for box in parsed_boxes:
            (x, y, w, h) = (box['left'], box['top'], box['width'], box['height'])
            cv2.rectangle(img_np, (x, y), (x + w, y + h), (0, 255, 0), 2)
        cv2.imwrite('result.png', img_np)
        txt = ''
        for j in range(len(parsed_boxes)):
            if parsed_boxes[j]['text'] == '':
                continue
            txt += parsed_boxes[j]['text'].strip(' ')
            txt += ' ' + str(parsed_boxes[j]['left']) + ' ' + str(parsed_boxes[j]['top']) + ' ' + str(parsed_boxes[j]['width']) + ' ' + str(parsed_boxes[j]['height']) + ' '
        print(txt)
        return txt

In [31]:
ocr_obj = ocr(df)
text = ocr_obj.view(0)

 0 0 718 1000 PROJECT BRIEF 329 76 107 11 DATE: 107 110 49 28 June 2, 1990    DATE: 179 110 -28 28 June 1, 195 116 49 10 1990 263 117 107 15 BRAND: 112 143 46 31 General Merchandising 178 144 174 13 ITEM: 394 147 33 10 Package Fixture      Circle-K  Nonspecific 452 148 -184 26 Convenient Storés 451 162 140 12 SUMMARY OF PROJECT: 110 184 155 14 See Attached 285 187 99 11 SUPPLIERS BEING CONSIDERED: 109 254 222 12 chicago show 107 280 101 71 Display 108 301 58 21 Equation 374 301 -133 21 Chicago Display 107 336 125 15 Robert Nielson & Associates 107 364 224 13 FUNDING: 106 406 64 44 1990 Customized Merchandising 107 434 240 16 Services 106 461 65 11 SPNS - 198 463 -10 9 SIGNATURE: 104 560 92 14 REQUESTING MANAGER 102 599 170 14 MERCHANDISING MANAGER 101 641 189 57 GROUP PRODUCT DIRECTOR 101 686 184 12 —    DEPARTMENT PURCHASING 282 721 -99 28 — 353 729 14 2 RETURN TO: 98 771 82 14 REQUESTING 199 772 83 13 | MANAGER 376 773 -27 10 4514cbta 98 827 66 10 


/var/folders/fv/pf_pqm6s2ds43tstk6b5q3wm0000gn/T/ipykernel_72369/3881488818.py:86: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  nparr = np.fromstring(img_str, np.uint8)


In [ ]:
text